# Capstone Project - The Battle of the Neighborhoods
### Applied Data Science Capstone by IBM/Coursera

## Introduction

Suppose you want to open a new gym, where should it be located? In this project we will go through the process of finding a location that is likely to be the optimal place to start.

In this scenario we want to open a new gym in one of the 20 biggest cities in The Netherlands. Ideally we would want a neighbourhood that is not already saturated with existing gyms, but is similar to other neighbourhoods with succesful gyms.


We will use publicly available data about the dutch cities and their neighbourhoods so we can employ various forms of data analytics and visualizations to help us in our search.

## Data

The metrics we have decided to use to find out new location are:
* Population density per existing gym in a city
* Amount of pre-existing gyms per neighbourhood
* Similarity of neighbourhood to other neighbourhoods with gyms

Following data sources will be needed to extract/generate the required information:
* Population statistics will be obtained from wikipedia
* Name and location of neighbourhoods in each city will be obtained by a combination of Google Maps API geocoding and the Postal code information per city
* Number of gyms and their location in every neighborhood will be obtained using the Foursquare API


In [1]:
import pandas as pd
import numpy as np

import requests
import bs4

In [2]:
response = requests.get('https://en.wikipedia.org/wiki/Template:Largest_cities_of_the_Netherlands')
html = bs4.BeautifulSoup(response.text, 'html.parser')
table = html.find('table',{'class':'navbox'})

We get our list of cities from the wikipedia page for the 20 largest cities of the netherlands. The table is only 10 rows because the data is spread over double the columns. We'll need to do some cleaning to get a nice dataset with no duplicate columns and exactly 20 rows.

In [4]:
#scrape the wikipedia table for its entries and combine those in the dataframe.
city_data = []
cycle_i = 0
cycle_j = 0
for i in table.findAll('tr'):
    row_data=[]
    if cycle_i <2: #skip some empty rows
        cycle_i += 1
        continue
    for j in i.findAll('td'):
        if cycle_i == 2 and (cycle_j == 0 or cycle_j == 9): #some image subscript is in the table that we can skip as well
            cycle_j += 1
            continue
        row_data.append(j.text.strip())
        cycle_j += 1
    cycle_i += 1
    city_data.append(row_data)
df =pd.DataFrame(city_data)

In [5]:
df1 = df.iloc[:,0:4].reset_index(drop=True).dropna()
df2 = df.iloc[:,4::].reset_index(drop=True).dropna()

In [6]:
df1.columns=['0','1','2','3']
df2.columns=['0','1','2','3']


Here we finally have a nice table. The Hague is renamed to "'s-Gravenhage". The former is the english name and the later is the dutch name is used the most in online databases.

In [7]:
df = df1.append(df2,sort=False)
df.columns = ['index','City','Region','Population']
df['City'].replace('The Hague',"'s-Gravenhage", inplace=True) 


In [8]:
from geopy.geocoders import Nominatim
geo_locator = Nominatim(user_agent ='Nederland', timeout=2)

In [9]:
import requests
import bs4

We use the Geonames API to retrieve all the postal codes registered to each city. Here we can also find the latitudes and longitudes for each location. 

In [10]:
postalcodes = []
latitudes = []
longitudes = []
places = []
municitality = []

for i in df['City']:
    response = requests.get('http://api.geonames.org/postalCodeSearch?username=xxxx&maxrows=200&country=NL&isReduced=True&style=long&placename=' + i)
    html = bs4.BeautifulSoup(response.text, 'html.parser')
    codes = html.find_all('postalcode')
    lats = html.find_all('lat')
    longs = html.find_all('lng')
    municipalities = html.find_all('adminname2')
    
    for j in range(len(codes)):
        postalcodes.append(codes[j].text)
        latitudes.append(lats[j].text)
        longitudes.append(longs[j].text)
        municitality.append(municipalities[j].text)

        places.append(i)
    



In [11]:
locations = pd.DataFrame({'Postal Code':postalcodes, 
                          'Latitude':latitudes,
                          'Longitude':longitudes,
                          'Place' :places,
                          'Municipality' : municitality})


Now we have a neat dataframe with our location data. We use the municipality data to distinguish between locations that are in Utrecht or Groningen the city and Utrecht or Groningen the province, as we only want the former.


In [13]:
locations = locations[locations['Municipality'] == locations['Place']]

In [14]:
locations.groupby('Place').count()

Postal Code  Latitude  Longitude  Municipality
Place                                                           
's-Gravenhage              61        61         61            61
's-Hertogenbosch           30        30         30            30
Almere                     43        43         43            43
Amersfoort                 18        18         18            18
Amsterdam                  81        81         81            81
Apeldoorn                  33        33         33            33
Arnhem                     26        26         26            26
Breda                      25        25         25            25
Eindhoven                  34        34         34            34
Enschede                   23        23         23            23
Groningen                  43        43         43            43
Haarlem                    20        20         20            20
Haarlemmermeer             33        33         33            33
Leiden                     16        16         16            16
Nijmegen                   25        25         25            25
Rotterdam                  79        79         79            79
Tilburg                    28        28         28            28
Utrecht                    46        46         46            46
Zaanstad                   23        23         23            23
Zwolle                     25        25         25            25

In [15]:
import folium

Let's create a map of the netherlands that shows all the locations we've gathered so far. We use a marker radius of 500 meters, the same we'll use in our foursquare search. As you can see there is some overlap, which we'll take care of later, and some empty spots.

In [16]:
# create map of The Netherlands
map_netherlands = folium.Map(location=[52.40451, 4.89127], zoom_start=10)

# add location markers to map
for lat, lng, postalcode, municipality in zip(locations['Latitude'], locations['Longitude'], locations['Postal Code'], locations['Municipality']):
        label = '{},{}'.format(postalcode, municipality)
        label = folium.Popup(label, parse_html=True)
        folium.Circle(
        [lat, lng],
        popup=label,
        radius=500,
        fill=True,
        fill_opacity=0.7,
        parse_html=False).add_to(map_netherlands)  
    
map_netherlands

Our foursquare credentials

In [17]:
CLIENT_ID = 'xxxxxx' # your Foursquare ID
CLIENT_SECRET = 'xxxxxx' # your Foursquare Secret
VERSION = '20200605' # Foursquare API version

Script to search foursquare for all venues near our selected locations

In [18]:
def getNearbyVenues(postalcode,city, latitudes, longitudes, radius=500):
    i = float(1)
    venues_list=[]
    for postalcode, city, lat, lng in zip(postalcode, city, latitudes, longitudes):
        print( i/(len(locations)/100) ) #show progress in output
        i +=1    
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        try:
            results = requests.get(url).json()["response"]['groups'][0]['items']
        
        
            # return only relevant information for each nearby venue
            venues_list.append([(
                city,
                postalcode, 
                lat, 
                lng, 
                v['venue']['name'], 
                v['venue']['location']['lat'], 
                v['venue']['location']['lng'],  
                v['venue']['categories'][0]['name']) for v in results])

        except:
            continue    
        
    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['City',
                'Postal Code', 
                'Neighborhood Latitude', 
                'Neighborhood Longitude', 
                'Venue', 
                'Venue Latitude', 
                'Venue Longitude', 
                'Venue Category']
    return(nearby_venues)

In [19]:
LIMIT = 100 # limit of number of venues returned by Foursquare API
radius = 500 # define radius
neighbourhood_venues = getNearbyVenues(postalcode=locations['Postal Code'],
                                   city=locations['Place'],
                                   latitudes=locations['Latitude'],
                                   longitudes=locations['Longitude']
                                  )

0.1404494382022472
0.2808988764044944
0.42134831460674155
0.5617977528089888
0.7022471910112359
0.8426966292134831
0.9831460674157303
1.1235955056179776
1.2640449438202248
1.4044943820224718
1.544943820224719
1.6853932584269662
1.8258426966292134
1.9662921348314606
2.106741573033708
2.247191011235955
2.3876404494382024
2.5280898876404496
2.6685393258426964
2.8089887640449436
2.9494382022471908
3.089887640449438
3.230337078651685
3.3707865168539324
3.5112359550561796
3.651685393258427
3.792134831460674
3.932584269662921
4.073033707865169
4.213483146067416
4.353932584269663
4.49438202247191
4.634831460674158
4.775280898876405
4.915730337078652
5.056179775280899
5.1966292134831455
5.337078651685393
5.47752808988764
5.617977528089887
5.758426966292134
5.8988764044943816
6.039325842696629
6.179775280898876
6.320224719101123
6.46067415730337
6.601123595505618
6.741573033707865
6.882022471910112
7.022471910112359
7.162921348314606
7.303370786516854
7.443820224719101
7.584269662921348
7.724719

Let's take a quick look at the venues we've gathered. From a quick scan it looks like the bigger cities have the most venues so that looks right.

In [22]:
neighbourhood_venues.groupby('City').size()

City
's-Gravenhage       2773
's-Hertogenbosch     605
Almere               757
Amersfoort           529
Amsterdam           4656
Apeldoorn            553
Arnhem               718
Breda                563
Eindhoven           1000
Enschede             500
Groningen           1246
Haarlem              947
Haarlemmermeer       640
Leiden               616
Nijmegen             818
Rotterdam           3321
Tilburg              729
Utrecht             1913
Zaanstad             422
Zwolle               538
dtype: int64

Here we query foursquare again, this time we only want the information for gyms and fitness centre (determined by category ID)

In [23]:
def getNearbyGyms(postalcode,city, latitudes, longitudes, radius=500):
    i = float(1)
    venues_list=[]
    for postalcode, city, lat, lng in zip(postalcode, city, latitudes, longitudes):
        print( i/(len(locations)/100) )
        i +=1    
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&categoryId=4bf58dd8d48988d175941735&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        try:
            results = requests.get(url).json()["response"]['groups'][0]['items']
        
        
            # return only relevant information for each nearby venue
            venues_list.append([(
                city,
                postalcode, 
                lat, 
                lng, 
                v['venue']['name'], 
                v['venue']['location']['lat'], 
                v['venue']['location']['lng'],  
                v['venue']['categories'][0]['name']) for v in results])

        except:
            continue    
        
    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['City',
                'Postal Code', 
                'Neighborhood Latitude', 
                'Neighborhood Longitude', 
                'Venue', 
                'Venue Latitude', 
                'Venue Longitude', 
                'Venue Category']
    return(nearby_venues)

In [96]:
LIMIT = 100 # limit of number of venues returned by Foursquare API
radius = 500 # define radius
neighbourhood_gyms = getNearbyGyms(postalcode=locations['Postal Code'],
                                   city=locations['Place'],
                                   latitudes=locations['Latitude'],
                                   longitudes=locations['Longitude']
                                  )

0.1404494382022472
0.2808988764044944
0.42134831460674155
0.5617977528089888
0.7022471910112359
0.8426966292134831
0.9831460674157303
1.1235955056179776
1.2640449438202248
1.4044943820224718
1.544943820224719
1.6853932584269662
1.8258426966292134
1.9662921348314606
2.106741573033708
2.247191011235955
2.3876404494382024
2.5280898876404496
2.6685393258426964
2.8089887640449436
2.9494382022471908
3.089887640449438
3.230337078651685
3.3707865168539324
3.5112359550561796
3.651685393258427
3.792134831460674
3.932584269662921
4.073033707865169
4.213483146067416
4.353932584269663
4.49438202247191
4.634831460674158
4.775280898876405
4.915730337078652
5.056179775280899
5.1966292134831455
5.337078651685393
5.47752808988764
5.617977528089887
5.758426966292134
5.8988764044943816
6.039325842696629
6.179775280898876
6.320224719101123
6.46067415730337
6.601123595505618
6.741573033707865
6.882022471910112
7.022471910112359
7.162921348314606
7.303370786516854
7.443820224719101
7.584269662921348
7.724719

In [97]:
neighbourhood_gyms.set_index('City', inplace= True)

Postal Code Neighborhood Latitude Neighborhood Longitude  \
City                                                                 
Amsterdam        1055              52.38017                4.85235   
Amsterdam        1055              52.38017                4.85235   
Amsterdam        1058              52.35789                4.85096   
Amsterdam        1058              52.35789                4.85096   
Amsterdam        1058              52.35789                4.85096   
...               ...                   ...                    ...   
Leiden           2333              52.16932                4.47319   
Leiden           2334              52.17247                4.48182   
Leiden           2334              52.17247                4.48182   
Leiden           2334              52.17247                4.48182   
Leiden           2334              52.17247                4.48182   

                                    Venue  Venue Latitude  Venue Longitude  \
City                                                                         
Amsterdam        Selin Health and Fitness       52.382017         4.846087   
Amsterdam                  CrossfitAKA WZ       52.382453         4.857626   
Amsterdam           David Lloyd Amsterdam       52.357457         4.856097   
Amsterdam  David Lloyd Swimming Pool Area       52.357432         4.856030   
Amsterdam                     Outdoor Gym       52.357350         4.848385   
...                                   ...             ...              ...   
Leiden         TSUKI meditatie en inzicht       52.171069         4.478718   
Leiden                     Wing Chun Tong       52.172657         4.485354   
Leiden         TSUKI meditatie en inzicht       52.171069         4.478718   
Leiden                 Praktijk voor Yoga       52.169693         4.483784   
Leiden       Atletiekbaan Leiden Atletiek       52.173527         4.478794   

                 Venue Category  
City                             
Amsterdam                   Gym  
Amsterdam        Gymnastics Gym  
Amsterdam  Gym / Fitness Center  
Amsterdam              Gym Pool  
Amsterdam                   Gym  
...                         ...  
Leiden              Yoga Studio  
Leiden     Gym / Fitness Center  
Leiden              Yoga Studio  
Leiden              Yoga Studio  
Leiden                    Track  

[1468 rows x 7 columns]

Use the gym location data to create new markers on our map. So we can see what our distribution is like. As expected the larger cities seem to have more sport facilities.

In [50]:
# add markers for each gym to the map
for lat, lng, postalcode, city in zip(neighbourhood_gyms['Venue Latitude'], neighbourhood_gyms['Venue Longitude'], neighbourhood_gyms['Postal Code'], neighbourhood_gyms.index):
        label = '{},{}'.format(postalcode, city)
        label = folium.Popup(label, parse_html=True)
        folium.CircleMarker(
        [lat, lng],
        popup=label,
        color='red',
        radius=3,
        fill=True,
        fill_opacity=0.7,
        parse_html=False).add_to(map_netherlands)  
    
map_netherlands

Let's see what our gym distribution is like. When we queried foursquare for data, some venues might have been found from different postal codes. To get an accurate total count per city we need to remove these duplicates. Now we can calculate the total amount of gyms per city, and the total population per gym density of each city (pop/#gyms)

In [98]:
total_gyms = neighbourhood_gyms.drop_duplicates(['Postal Code','Venue Latitude','Venue Longitude','Venue']).groupby('City')['Venue'].count() #total gyms without the duplicates that are registered to different postal codes

In [103]:
df = df.join(total_gyms, on = 'City')
df.columns = ['index','City','Region','Population', 'Total Gyms']

df['gym density'] = df['Population'].str.replace(",","").astype(int)/df['Total Gyms'] #calculate the population/gym density for each city

In [104]:
top_cities = df.sort_values(by = 'gym density', ascending = False).head(3) #Make a selection of the 3 cities with the highest population per gym

We want to start making clusters based on the top 10 most common venues per area. This way we can try to find similarities between neighbourhoods with gyms, and locations that are not saturated yet.

In [105]:
neighbourhood_grouped = neighbourhood_onehot.groupby('Postal Code').sum().reset_index() 

In [106]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [ ]:
# one hot encoding
neighbourhood_onehot = pd.get_dummies(neighbourhood_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
neighbourhood_onehot['Postal Code'] = neighbourhood_venues['Postal Code'] 
neighbourhood_onehot['City'] = neighbourhood_venues['City']

# move neighborhood column to the first column
fixed_columns = [neighbourhood_onehot.columns[-2]] + list(neighbourhood_onehot.columns[:-2])
neighbourhood_onehot = neighbourhood_onehot[fixed_columns]

In [107]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Postal Code']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Postal Code'] = neighbourhood_grouped['Postal Code']

for ind in np.arange(neighbourhood_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(neighbourhood_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Postal Code 1st Most Common Venue 2nd Most Common Venue  \
0        1011                 Hotel                   Bar   
1        1012                 Hotel                   Bar   
2        1013                   Bar            Restaurant   
3        1014            Restaurant             Nightclub   
4        1015                 Hotel                   Bar   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0           Coffee Shop            Restaurant                 Plaza   
1           Coffee Shop            Restaurant                   Pub   
2           Coffee Shop                  Café    Italian Restaurant   
3           Music Venue    Italian Restaurant                   Bar   
4                  Café           Coffee Shop        Sandwich Place   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0                   Pub     French Restaurant        Breakfast Spot   
1     French Restaurant        Sandwich Place          Dessert Shop   
2           Yoga Studio             BBQ Joint                Bakery   
3           Coffee Shop                  Café           Snack Place   
4    Italian Restaurant           Cheese Shop          Cocktail Bar   

  9th Most Common Venue 10th Most Common Venue  
0        History Museum                 Church  
1              Beer Bar              Bookstore  
2      Tapas Restaurant   Marijuana Dispensary  
3                  Farm                  Hotel  
4     French Restaurant                  Plaza

We use KMeans clustered to determine 5 different types of neighbourhoods based on their 10 most common venues.

In [108]:
from sklearn.cluster import KMeans
kclusters = 5
neighbourhood_grouped_clustering = neighbourhood_grouped.drop('Postal Code',1)

In [109]:
kmeans = KMeans(n_clusters=kclusters).fit(neighbourhood_grouped_clustering)

In [110]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

neighbourhood_merged = locations

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
neighbourhood_merged = neighbourhood_merged.join(neighborhoods_venues_sorted.set_index('Postal Code'), on='Postal Code')

neighbourhood_merged.dropna(inplace=True)
neighbourhood_merged.head() # check the last columns!

Postal Code  Latitude Longitude      Place Municipality  Cluster Labels  \
0        1055  52.38017   4.85235  Amsterdam    Amsterdam             3.0   
1        1058  52.35789   4.85096  Amsterdam    Amsterdam             1.0   
2        1062  52.35483   4.83808  Amsterdam    Amsterdam             3.0   
3        1066    52.346   4.81634  Amsterdam    Amsterdam             3.0   
4        1068  52.35923   4.80521  Amsterdam    Amsterdam             2.0   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0                Bakery           Supermarket            Restaurant   
1            Restaurant                   Bar           Coffee Shop   
2           Supermarket        Sandwich Place           Coffee Shop   
3          Tram Station                 Hotel            Restaurant   
4           Supermarket    Turkish Restaurant                 Hotel   

   4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0                   Café                   Bar           Coffee Shop   
1         Breakfast Spot                  Café    Italian Restaurant   
2                   Café                 Plaza                 Hotel   
3               Bus Stop                  Café                Resort   
4  Indonesian Restaurant        Clothing Store               Theater   

  7th Most Common Venue 8th Most Common Venue          9th Most Common Venue  \
0                  Park            Bagel Shop  Vegetarian / Vegan Restaurant   
1                Bistro                Bakery                          Hotel   
2                   Gym    Italian Restaurant                   Tram Station   
3           Flower Shop             Nightclub                    Snack Place   
4             Drugstore  Gym / Fitness Center                  Shopping Mall   

  10th Most Common Venue  
0  Indonesian Restaurant  
1            Pizza Place  
2     Chinese Restaurant  
3                 Buffet  
4            Snack Place

In [111]:
import matplotlib.cm as cm
import matplotlib.colors as colors

Let's Create another map so we can see what the distribution of our clusters look like.

In [112]:
#create new map where the locations are clustered
map_netherlands_clustered = folium.Map(location=[52.40451, 4.89127], zoom_start=10)

x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]


# add markers to map
for lat, lng, city, postal_code, cluster in zip(neighbourhood_merged['Latitude'], neighbourhood_merged['Longitude'], neighbourhood_merged['Place'], neighbourhood_merged['Postal Code'], neighbourhood_merged['Cluster Labels']):
    label = '{}, {}'.format(postal_code, city)
    label = folium.Popup(label, parse_html=True)
    folium.Circle(
        [lat, lng],
        radius=500,
        popup=label,
        color=rainbow[int(cluster-1)],
        fill=True,
        fill_color=rainbow[int(cluster-1)],
        fill_opacity=0.7,
        parse_html=False).add_to(map_netherlands_clustered)  
    
map_netherlands_clustered

Now add the locations of our gyms and we might get some insights

In [113]:
# add all the gyms to the clustered map
for lat, lng, postalcode, city in zip(neighbourhood_gyms['Venue Latitude'], neighbourhood_gyms['Venue Longitude'], neighbourhood_gyms['Postal Code'], neighbourhood_gyms.index):
        label = '{},{}'.format(postalcode, city)
        label = folium.Popup(label, parse_html=True)
        folium.CircleMarker(
        [lat, lng],
        popup=label,
        color='black',
        radius=3,
        fill=True,
        fill_opacity=0.7,
        parse_html=False).add_to(map_netherlands_clustered)  
    
map_netherlands_clustered

In order to find the prime locations, we want to know which locations have fewer gyms than their cluster average.

In [114]:
neighbourhoods = neighbourhood_merged[['Postal Code', 'Cluster Labels', 'Place']] # create a new dataframe 

In [115]:
neighbourhood_gym_cluster = neighbourhoods.join(neighbourhood_gyms.groupby('Postal Code')['Venue'].count(), on = 'Postal Code').sort_values('Venue', ascending = False) # count total amount of gyms per location

In [134]:
top_neighbourhoods = neighbourhood_gym_cluster.groupby('Cluster Labels')['Venue'].mean().sort_values(ascending=False).reset_index() # calculate average amount of gyms per location for each cluster
top_neighbourhoods.rename(columns = {'Venue':'Venue Average'}, inplace=True)
top_neighbourhoods.set_index('Cluster Labels', inplace=True)


In [141]:
neighbourhood_gym_data = neighbourhood_gym_cluster.join(top_neighbourhoods, on = 'Cluster Labels')

We make a selection of all the locations where the amount of gyms is lower than their cluster average, while located in one of the top 3 cities with the highest pop/gym density

In [181]:
#some locations have no gym,so we need to fill na with zeroes. 
neighbourhood_gym_data.fillna(0)
top_locations = neighbourhood_gym_data[((neighbourhood_gym_data['Venue'] < neighbourhood_gym_data['Venue Average']) & (neighbourhood_gym_data['Place'].isin(top_cities['City'])))].sort_values('Place')
top_locations = top_locations.set_index('Postal Code').join( locations.set_index('Postal Code'), on='Postal Code', how = 'inner',lsuffix='_l_',rsuffix='_r_')
top_locations.reset_index(inplace=True)

Create another map to visualize the prime locations

In [182]:
# create map of New York using latitude and longitude values
map_gyms = folium.Map(location=[52.40451, 4.89127], zoom_start=10)

# add markers to map
for lat, lng, postalcode, municipality in zip(top_locations['Latitude'], top_locations['Longitude'], top_locations['Postal Code'], top_locations['Municipality']):
        label = '{},{}'.format(postalcode, municipality)
        label = folium.Popup(label, parse_html=True)
        folium.Circle(
        [lat, lng],
        popup=label,
        radius=500,
        fill=True,
        fill_opacity=0.7,
        parse_html=False).add_to(map_gyms)  
    
map_gyms

In [183]:
top_locations # list of all the locations

Postal Code  Cluster Labels          Place_l_  Venue  Venue Average  \
0         5212             1.0  's-Hertogenbosch    3.0       3.750000   
1         5235             2.0  's-Hertogenbosch    2.0       2.536458   
2         5232             0.0  's-Hertogenbosch    1.0       1.928058   
3         5223             3.0  's-Hertogenbosch    2.0       3.065934   
4         5233             2.0  's-Hertogenbosch    1.0       2.536458   
5         5243             0.0  's-Hertogenbosch    1.0       1.928058   
6         5391             0.0  's-Hertogenbosch    1.0       1.928058   
7         5242             0.0  's-Hertogenbosch    1.0       1.928058   
8         5247             0.0  's-Hertogenbosch    1.0       1.928058   
9         5213             2.0  's-Hertogenbosch    1.0       2.536458   
10        5221             0.0  's-Hertogenbosch    1.0       1.928058   
11        5241             0.0  's-Hertogenbosch    1.0       1.928058   
12        7531             0.0          Enschede    1.0       1.928058   
13        7548             0.0          Enschede    1.0       1.928058   
14        7532             2.0          Enschede    1.0       2.536458   
15        7546             2.0          Enschede    1.0       2.536458   
16        7545             2.0          Enschede    1.0       2.536458   
17        7544             2.0          Enschede    2.0       2.536458   
18        7512             3.0          Enschede    2.0       3.065934   
19        7521             2.0          Enschede    2.0       2.536458   
20        7543             2.0          Enschede    1.0       2.536458   
21        2165             0.0    Haarlemmermeer    1.0       1.928058   
22        1119             0.0    Haarlemmermeer    1.0       1.928058   
23        2144             0.0    Haarlemmermeer    1.0       1.928058   
24        2154             0.0    Haarlemmermeer    1.0       1.928058   
25        1165             2.0    Haarlemmermeer    1.0       2.536458   
26        1437             0.0    Haarlemmermeer    1.0       1.928058   
27        1171             2.0    Haarlemmermeer    1.0       2.536458   
28        2132             3.0    Haarlemmermeer    1.0       3.065934   
29        2155             0.0    Haarlemmermeer    1.0       1.928058   
30        2134             2.0    Haarlemmermeer    2.0       2.536458   
31        2131             3.0    Haarlemmermeer    2.0       3.065934   
32        2141             0.0    Haarlemmermeer    1.0       1.928058   

    Latitude Longitude          Place_r_      Municipality  
0   51.69696   5.30934  's-Hertogenbosch  's-Hertogenbosch  
1   51.72661   5.30774  's-Hertogenbosch  's-Hertogenbosch  
2   51.70726   5.32921  's-Hertogenbosch  's-Hertogenbosch  
3   51.69075   5.28209  's-Hertogenbosch  's-Hertogenbosch  
4   51.71509     5.321  's-Hertogenbosch  's-Hertogenbosch  
5   51.72078     5.371  's-Hertogenbosch  's-Hertogenbosch  
6   51.72604   5.43688  's-Hertogenbosch  's-Hertogenbosch  
7   51.71052   5.36861  's-Hertogenbosch  's-Hertogenbosch  
8   51.73099   5.36663  's-Hertogenbosch  's-Hertogenbosch  
9   51.69487   5.32595  's-Hertogenbosch  's-Hertogenbosch  
10  51.72401   5.25814  's-Hertogenbosch  's-Hertogenbosch  
11  51.71784   5.35822  's-Hertogenbosch  's-Hertogenbosch  
12   52.2294   6.91642          Enschede          Enschede  
13  52.20158   6.79638          Enschede          Enschede  
14  52.22013    6.9615          Enschede          Enschede  
15  52.19279   6.85314          Enschede          Enschede  
16  52.21253   6.86413          Enschede          Enschede  
17  52.19212    6.8776          Enschede          Enschede  
18  52.21381   6.89781          Enschede          Enschede  
19  52.22904   6.86162          Enschede          Enschede  
20  52.20561   6.87713          Enschede          Enschede  
21  52.25607   4.57358    Haarlemmermeer    Haarlemmermeer  
22   52.2795   4.75479    Haarlemmermeer    Haarlemmermeer  
23  52.28678   4.59575

Here we have a list of 32 locations that have fewer gyms than the average comparable location, and are situated in the 3 cities with the fewest gyms. This should be a good starting point for determining where to start a new Gym.